In [3]:
import sys
sys.path.append('..')
from tool import *
from statistics import mean
from astropy.visualization import LogStretch
from astropy.visualization.mpl_normalize import ImageNormalize
from matplotlib.ticker import MultipleLocator
from sklearn.utils import shuffle
import mpl_scatter_density

In [2]:
def fill_albedo2(month,type,sza_L,landcover_type,interp_2000=False):
    max_distance=3
    if type=='snow':
        distence_w_dim=torch.load(f'/data2/hzy/albedo2/data/weight_LCCS2.pth')[type]
    else:
        distence_w_dim=torch.load(f'/data2/hzy/albedo2/data/weight_{landcover_type}.pth')[type]
    sza_L_month=sza_L[0,month-1]
    bands=['albedo_BSA_vis', 
        'albedo_WSA_vis', 
        'albedo_BSA_nir', 
        'albedo_WSA_nir', 
        'albedo_BSA_shortwave', 
        'albedo_WSA_shortwave']
    m_index=[(month-2)%12+1,(month-1)%12+1,(month)%12+1]
    offset=[1 if m_index[j]-m_index[0]>=0 else -1 for j in range(len(m_index))]
    if np.array(offset).sum()==len(offset):
        offset=[0]*len(m_index)
    vs=[]
    ms=[]
    land_proportions=[]
    for i in range(len(offset)): 
        NC=nc.Dataset(f'/data2/hzy/albedo2/albedo_information_nc2/nan_to_2000/month_{m_index[i]}_{landcover_type}.nc','r')
        for band in bands:
            vs.append(NC.variables[f'{band}-{type}'][:])
        if type!='ocean':
            ms.append(NC.variables[f'area-{type}'][:])
        # qa=NC.variables['qa'][:]
        area_grid=NC.variables['area-grid'][:]
        area_land=NC.variables['area-land'][:]
        land_proportions.append(area_land/area_grid)
        NC.close()
    offset_bands=[]
    for i in offset:
        offset_bands+=[i]*len(bands)
    if offset[0]!=0:
        nan_array=np.zeros((1,180,360))*np.nan
        vs=[np.concatenate((nan_array,vs[i]),axis=0) if offset_bands[i]==1 else np.concatenate((vs[i],nan_array),axis=0) for i in range(len(offset_bands))]
        land_proportions=[np.concatenate((nan_array,land_proportions[i]),axis=0) if offset[i]==1 else np.concatenate((land_proportions[i],nan_array),axis=0) for i in range(len(offset))]
        if type!='ocean':
            ms=[np.concatenate((nan_array,ms[i]),axis=0) if offset[i]==1 else np.concatenate((ms[i],nan_array),axis=0) for i in range(len(offset))]
        else:
            ms=land_proportions  
    else:
        if type=='ocean':
            ms=land_proportions  
    M,H,W=vs[0].shape
    v=np.stack(vs).reshape((len(offset),len(bands),M,H,W)).transpose((1,0,2,3,4))
    m=np.stack(ms)
    all_indices = np.indices(v[0].shape).reshape(4, -1).T
  
    if interp_2000:
        if type!='ocean':
                interp_indices = all_indices[((v[0]==2000) & (m>0)).reshape(-1)]
        else:
            interp_indices = all_indices[((v[0]==2000) & (m<1) & (m>0)).reshape(-1)]
        nonan_indices=all_indices[((~np.isnan(v[0])).reshape(-1)) & ((v[0]!=2000).reshape(-1))]
    else:
        if type!='ocean':
            interp_indices = all_indices[(np.isnan(v[0]) & (m>0)).reshape(-1)]
        else:
            interp_indices = all_indices[(np.isnan(v[0]) & (m<1) & (m>0)).reshape(-1)]
        nonan_indices=all_indices[(~np.isnan(v[0])).reshape(-1)]

    interp_indices=[j for j in interp_indices if j[0]==int(len(offset)/2)]  
    interp_indices=[j for j in interp_indices if sza_L_month[j[2],j[3]]<2]
    nonan_indices2=[j for j in nonan_indices if j[0]==int(len(offset)/2)]  
    nonan_indices2=[j for j in nonan_indices2 if sza_L_month[j[2],j[3]]<2]
    str_output=f'{month}-{type}  '+str(len(interp_indices))+'  '+str(round(len(interp_indices)/(len(nonan_indices2)+len(interp_indices)+0.01)*100,2))+'%'

    time.sleep(1)
    kk=[search_nonan2(v,interp_indice,max_distance=max_distance,distence_w_dim=distence_w_dim,interp_2000=interp_2000) for interp_indice in tqdm(interp_indices,desc=str_output)]
    interp_values=np.array([a[0] for a in kk])
    dws=np.array([a[1] for a in kk])
    dws_v=np.zeros(v.shape)
    for z in range(len(interp_indices)):
        v[:,interp_indices[z][0],interp_indices[z][1],interp_indices[z][2],interp_indices[z][3]]=np.array(interp_values[z])
        dws_v[:,interp_indices[z][0],interp_indices[z][1],interp_indices[z][2],interp_indices[z][3]]=np.array(dws[z])
    if offset[int(len(offset)/2)]>=0:
        return v[:,int(len(offset)/2),offset[int(len(offset)/2)]:],dws_v[:,int(len(offset)/2),offset[int(len(offset)/2)]:]
    else:
        return v[:,int(len(offset)/2),:-1],dws_v[:,int(len(offset)/2),:-1]
def TS_IDW_4d_2(v,interp_indice,max_distance,distence_w_dim,interp_2000):
        value=v[zero(interp_indice[0]-int(max_distance/distence_w_dim[0])):interp_indice[0]+int(max_distance/distence_w_dim[0])+1,
                zero(interp_indice[1]-int(max_distance/distence_w_dim[1])):interp_indice[1]+int(max_distance/distence_w_dim[1])+1,
                zero(interp_indice[2]-int(max_distance/distence_w_dim[2])):interp_indice[2]+int(max_distance/distence_w_dim[2])+1,
                zero(interp_indice[3]-int(max_distance/distence_w_dim[3])):interp_indice[3]+int(max_distance/distence_w_dim[3])+1]
        non_nan_indices = np.where(~np.isnan(value))
        if interp_2000:
            v[v==2000]=np.nan
        non_nan_points = np.array(list(zip(non_nan_indices[0], non_nan_indices[1], non_nan_indices[2],non_nan_indices[3])))
        if len(non_nan_points)==0:
                interpolated_value=np.nan
                dws=np.nan
        else:
                k=np.array([zero(-interp_indice[0]+int(max_distance/distence_w_dim[0]))-int(max_distance/distence_w_dim[0]),
                        zero(-interp_indice[1]+int(max_distance/distence_w_dim[1]))-int(max_distance/distence_w_dim[1]),
                        zero(-interp_indice[2]+int(max_distance/distence_w_dim[2]))-int(max_distance/distence_w_dim[2]),
                        zero(-interp_indice[3]+int(max_distance/distence_w_dim[3]))-int(max_distance/distence_w_dim[3])])
                non_nan_points+=k
                distance_s = np.array([np.linalg.norm(np.array(non_nan_points[i])*np.array(distence_w_dim)) for i in range(len(non_nan_points))])
                if len(distance_s)<10:
                        interpolated_value=np.nan
                        dws=np.nan
                else:
                        kth = np.partition(distance_s, 9)[9]
                        distance=distance_s.copy()
                        distance1=distance_s.copy()
                        distance1=distance1[distance_s<=kth]
                        weights = 1.0 / distance1**2
                        dws=np.sum(weights)
                        weights /= dws
                        non_nan_values = value[non_nan_indices]
                        non_nan_values=non_nan_values[distance<=kth]
                        interpolated_value = np.sum(weights * non_nan_values)
        return interpolated_value,dws
    
def search_nonan2(v,interp_indice,max_distance,distence_w_dim,interp_2000):
    k_bands=[]
    dws_bands=[]
    search_n=1
    for i in range(6):
        k,dws=TS_IDW_4d_2(v[i],interp_indice,max_distance=max_distance*search_n,distence_w_dim=distence_w_dim[i],interp_2000=interp_2000)
        while np.isnan(k):
            search_n*=2
            k,dws=TS_IDW_4d_2(v[i],interp_indice,max_distance=max_distance*search_n,distence_w_dim=distence_w_dim[i],interp_2000=interp_2000)
        k_bands.append(k)
        dws_bands.append(dws)
    
    return k_bands,dws_bands
def zero(k):
    if k<0:
        return 0
    else:
        return k
for landcover_type in ['IGBP']:
    if landcover_type=='LCCS2':
        lc_len=10
    elif landcover_type=='LCCS3':
        lc_len=9
    elif landcover_type=='IGBP':
        lc_len=16
    elif landcover_type=='LCCS1':
        lc_len=15 
    bands=['albedo_BSA_vis', 
    'albedo_WSA_vis', 
    'albedo_BSA_nir', 
    'albedo_WSA_nir', 
    'albedo_BSA_shortwave',
    'albedo_WSA_shortwave']
    _,sza_L=torch.load(root_path+'sza_and_szaL.pth')
    landtypes=['landtype'+str(i) for i in range(1,lc_len+1)]+['snow']
    for month in range(1,13):
        print(landcover_type)
        NC=nc.Dataset(f'/data2/hzy/albedo2/albedo_information_nc2/nan_to_2000_fill/month_{month}_{landcover_type}.nc','r+')
        for type in landtypes:
            if type=='landtype2':
                continue
            v_fill,dws=fill_albedo2(month,type,sza_L,landcover_type,True)
            for band_i in range(len(bands)):
                
                NC.variables[f'{bands[band_i]}-{type}'][:]=v_fill[band_i]
                try:
                    NC.createVariable(f'DWS-{type}-{bands[band_i]}', 'f4', ("time", "latitude", "longitude"))
                except:
                    pass
                    # print(f'DWS-{type}-{bands[band_i]} have existed')
                NC.variables[f'DWS-{type}-{bands[band_i]}'][:]=dws[band_i]
        NC.close()

In [4]:
#Fill the missing values at the validation points.
for landcover_type in ['LCCS1','LCCS2','LCCS3','IGBP']:
    if landcover_type=='LCCS2':
        lc_len=10
    elif landcover_type=='LCCS3':
        lc_len=9
    elif landcover_type=='IGBP':
        lc_len=16
    elif landcover_type=='LCCS1':
        lc_len=15  
    aaa_pd=pd.read_csv(f'/data2/hzy/albedo2/data/nan_coords2_{landcover_type}.csv')
    aaa2=[]
    landtypes=['landtype'+str(i) for i in range(1,lc_len)]+['snow']
    bands=['albedo_BSA_vis', 
        'albedo_WSA_vis', 
        'albedo_BSA_nir', 
        'albedo_WSA_nir', 
        'albedo_BSA_shortwave', 
        'albedo_WSA_shortwave']
    for m in range(1,13):
        print(m)
        NC=nc.Dataset(f'/data2/hzy/albedo2/albedo_information_nc2/nan_to_2000_fill/month_{m}_{landcover_type}.nc','r')
        for landtype in landtypes:
            kk={}
            aa_type=aaa_pd[(aaa_pd.type==landtype) & (aaa_pd.m==m)]
            n=0
            for band in bands:
                img=NC.variables[f'{band}-{landtype}'][:]
                kk[band]=[]
                for ind, row in aa_type.iterrows():
                    kk[band].append(img[row['y']-2001,90-row['lat'],row['lon']+180])
                n+=1
                aa_type[f'pred_band{n}']=kk[band]
            aaa2.append(aa_type)
        NC.close()
    aaa_pd2=pd.concat(aaa2)
    aaa_pd2.to_csv(f'/data2/hzy/albedo2/data/nan_coords3_{landcover_type}.csv')

1
2
3
4
5
6
7
8
9
10
11
12
1
2
3
4
5
6
7
8
9
10
11
12
1


In [4]:


bandss=['albedo_Black-sky_visible', 
    'albedo_White-sky_visible', 
    'albedo_Black-sky_near-infrared', 
    'albedo_White-sky_near-infrared', 
    'albedo_Black-sky_shortwave', 
    'albedo_White-sky_shortwave']
for kk in [[0,1],[2,3],[4,5]]:

    bands=[bandss[i] for i in kk]
    fig = plt.figure(figsize=(15, 25), dpi=600)
    for landcover_type_i in range(4):
        landcover_type=['LCCS1','LCCS2','LCCS3','IGBP'][landcover_type_i]
        aaa_pd2=pd.read_csv(f'/data2/hzy/albedo2/data/nan_coords3_{landcover_type}.csv')
        print(len(aaa_pd2))
        aaa_pd2=aaa_pd2.dropna(how='any')#无snow+snowfree 的nan像元，但有snowfree的nan
        print(len(aaa_pd2))
        aaa_pd2 = shuffle(aaa_pd2)[:500000]
        print('band    R2    RMSE')
        for n in kk:
            r2=r2_score(np.array(aaa_pd2[f'main_band{n+1}'])/1000,np.array(aaa_pd2[f'pred_band{n+1}'])/1000)
            rmse=np.sqrt(mean_squared_error(np.array(aaa_pd2[f'main_band{n+1}'])/1000,np.array(aaa_pd2[f'pred_band{n+1}'])/1000))
            print(bandss[n],r2,rmse)
          
        for wb_i in range(2):
            iii=landcover_type_i*2+wb_i+1
            plt.rcParams['font.sans-serif']=['Microsoft YaHei'] 
            x,y=np.array(aaa_pd2[f'pred_band{kk[wb_i]+1}'])/1000,np.array(aaa_pd2[f'main_band{kk[wb_i]+1}'])/1000
            R2 = r2_score(x,y)
            xy = np.vstack([x, y])
            def slope(xs, ys):
                m = (((mean(xs) * mean(ys)) - mean(xs * ys)) / ((mean(xs) * mean(xs)) - mean(xs * xs)))
                b = mean(ys) - m * mean(xs)
                return m, b
            k, b = slope(x, y)
            regression_line = []
            for a in range(100000):
                regression_line.append((k * a/100000) + b)
                
            MSE = mean_squared_error(y,x)  
            RMSE = np.power(MSE, 0.5)
            R2 = r2_score(y,x)
            norm = ImageNormalize(vmin=0., vmax=3000, stretch=LogStretch())
            ax = fig.add_subplot(4, 2, iii, projection='scatter_density')
            density = ax.scatter_density(x, y, cmap='GnBu',norm=norm)
            cbar=fig.colorbar(density, shrink=1, orientation='vertical', extend='both', pad=0.01, aspect=30, label='Frequency')
            cbar.ax.yaxis.set_major_locator(MultipleLocator(1000))
            ax.grid(True, linestyle='--', alpha=0.2)
            plt.annotate(landcover_type,(0.73,0.2))
            plt.annotate(f'Obs.={len(aaa_pd2)}',(0.73,0.15))
            plt.annotate('$R^2=%.3f$' % R2,(0.73,0.1))
            plt.annotate('$RMSE=%.3f$' % RMSE,(0.73,0.05))
            plt.xlabel(r'Four-dimensional spatiotemporal IDW predictions',fontsize=10)
            wb,bb=bands[wb_i].split('_')[1],bands[wb_i].split('_')[2]
            plt.ylabel(f'Ground truth ({wb} {bb})',fontsize=10)
            plt.axis([0, 1, 0,1])  # 设置线的范围
            ax.legend(loc='upper left', frameon = False)
    plt.savefig(f'../figure/IDW_val_{bb}.pdf',dpi=600)
    plt.show()

671704
658470
band    R2    RMSE
albedo_Black-sky_visible 0.9873176520387674 0.03148790580576501
albedo_White-sky_visible 0.9872417563890589 0.031040230351161175


No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.


541093
533753
band    R2    RMSE
albedo_Black-sky_visible 0.9873947950699927 0.03345985054084854
albedo_White-sky_visible 0.9872628208044512 0.03304665747155208


No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.


546392
534291
band    R2    RMSE
albedo_Black-sky_visible 0.9867749177003001 0.03445277538856314
albedo_White-sky_visible 0.9866166551354227 0.03407304400995806


...

No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.


546392
534291
band    R2    RMSE
albedo_Black-sky_shortwave 0.9849510913493091 0.0282471417281536
albedo_White-sky_shortwave 0.98419694683617 0.027941981176518072


No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.


719150
706932
band    R2    RMSE
albedo_Black-sky_shortwave 0.9862798138354416 0.024173202966762973
albedo_White-sky_shortwave 0.9855379780250783 0.023907184891851552


No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
